# Assign modules

In [7]:
# Function to find images with the same prefix
def find_identical_images(column):
    # Dictionary to store filenames with the same prefix
    column = column.dropna()
    identical_images = {}
    # Iterate over each filename in the column
    for filename in column:
        # Get the prefix up to '_v'
        if filename[-6] == 'v':
            prefix = filename[:-5]
            # Add filename to the dictionary
            if prefix in identical_images:
                identical_images[prefix].append(filename)
            else:
                identical_images[prefix] = [filename]
    # Filter out prefixes with fewer than 2 filenames
    identical_images = {k: v for k, v in identical_images.items() if len(v) >= 2}            
    return identical_images


# Function to find columns in df where image filenames do not contain the keys from identical_images
def find_columns_without_identical_images(df, n, identical_images):
    columns_not_containing_nth_key = []
    nth_key = list(identical_images.keys())[n]
    for column in df.columns:
        # Check if any filename in the column contains the nth key
        if not any(nth_key in filename for filename in df[column].dropna()):
            columns_not_containing_nth_key.append(column)
    return columns_not_containing_nth_key

def swap_image_names(modules, column,identical_images, current_key, columns_without_identical_images):
    # Extract the value[0] corresponding to the current key
    current_value = identical_images[current_key][0]
    current_index = modules[modules[column] == current_value].index.tolist()[0]
    exchange_column = columns_without_identical_images[0]
    # Iterate over the image names in columns_not_containing_nth_key[0]
    for idx, filename in enumerate(modules[exchange_column]):
        # Check if the filename[-6] is not "v"
        if filename[-6] != 'v':
            # Check if the filename does not exist in the original modules[column]
            exact_match = any(filename == x for x in modules[column])
            if not exact_match:
                # Swap the image names
                modules[column][current_index], modules[exchange_column][idx] = filename, current_value
                break  # Stop after the first swap

In [36]:
import pandas as pd

# read file
modules = pd.read_csv('Module_assign/youthful_module.csv')
outputpath = 'Module_assign_modify/youthful_module.csv'

In [37]:
for i, column in enumerate(modules.columns):
    print(column)
    columns_num = modules.shape[1]
    identical_images = find_identical_images(modules[column])
    for n in range(len(identical_images)):
        current_key = list(identical_images.keys())[n]
        count = modules.apply(lambda row: row.str.contains(current_key)).sum().sum()
        if count > columns_num:
            print(f'{current_key}:{count}')
        else:
            columns_without_identical_images = find_columns_without_identical_images(modules, n, identical_images)
            swap_image_names(modules, column,identical_images, current_key, columns_without_identical_images)
modules.to_csv(outputpath, index=False) 

Module1
Module2
Module3
Module4
Module5
Module6
Module7


In [38]:
new_modules = pd.read_csv(outputpath)
for i, column in enumerate(new_modules.columns):
    identical_images = find_identical_images(new_modules[column])
    print(identical_images)
    duplicates = new_modules.iloc[:, i][new_modules.iloc[:, i].duplicated()]
    print(duplicates)
    


{}
Series([], Name: Module1, dtype: object)
{}
Series([], Name: Module2, dtype: object)
{}
Series([], Name: Module3, dtype: object)
{}
Series([], Name: Module4, dtype: object)
{}
Series([], Name: Module5, dtype: object)
{}
Series([], Name: Module6, dtype: object)
{}
Series([], Name: Module7, dtype: object)


# Save modules to txt

In [32]:
import pandas as pd
import os

# Set the path to the folder containing the images
images_folder = "/Users/ruoyingzheng/Desktop/experimentProgram/images_ps"
# Get a list of all image files in the images folder
image_files = [f for f in os.listdir(images_folder) if os.path.isfile(os.path.join(images_folder, f)) and f.lower().endswith(('.jpg', '.jpeg', '.png', '.gif'))]

output_folder = "moduleStimuli_supp"
atten_check_output_folder = 'attenCheckStimuli_supp'

outputpath = 'Module_assign_modify/open_module.csv'
trait = 'open'
new_modules = pd.read_csv(outputpath)

In [33]:
if trait == 'attractive' or trait == 'feminine':
    num_atten = 4 # Number of attantion check
    index_atten = [30,60,90,120] # index of attention check images
elif trait == 'dominant':
    num_atten = 4 # Number of attantion check
    index_atten = [40,80,120,160] # index of attention check images
elif trait == 'youthful' or trait == 'warm':
    num_atten = 4 # Number of attantion check
    index_atten = [60,120,180,240] # index of attention check images
elif trait == 'competent' or trait == 'open':
    num_atten = 5 # Number of attantion check
    index_atten = [50,100,150,200,250] # index of attention check images

In [34]:
# Find replicated images - different target person in same images
# As the images are named as originalName_v1.jpg, so we compare the originalName_v to find the same image

replicated_images = {}

for image_file in image_files:
    # Extract the key (words before the fifth-to-last character)
    if image_file[-6] == 'v':
        key = image_file[:-5]
        
        # Check if the key already exists in the replicated_images dictionary
        if key in replicated_images:
            replicated_images[key].append(image_file)
        else:
            replicated_images[key] = [image_file]

replicated_images = {key: value for key, value in replicated_images.items() if len(value) > 1}


In [35]:
import random

# Iterate over columns
for column in new_modules.columns:
    # Define the file name
    filename = f"moduleStimuli_supp/{trait}_supp{column}.txt"
    # Extract the column data
    column_data = new_modules[column].dropna()

    # Shuffle the column data
    module = list(column_data)
    random.shuffle(module)

    # find image with more than one target person
    multitarget = []
    for item in module:
        if any(item.startswith(key) for key in replicated_images.keys()):
            multitarget.append(item)

    # Select attention check image
    atten_check_images = []
    atten_check_images = random.sample(multitarget, num_atten)

    # Select another relative images for attention check and Store attention check images
    atten_check_both=[]
    # Iterate for each images to find the same image but with another target person
    for i in range(len(atten_check_images)):
        atten_check_image1 = atten_check_images[i]
        # select another image which is the same as attention check image but with another target person
        atten_check_images_list = replicated_images[atten_check_image1[0:-5]].copy()
        atten_check_images_list.remove(atten_check_image1)
        atten_check_image2 = random.choice(atten_check_images_list)
        atten_check_both.append([atten_check_image1, atten_check_image2])

    txt_filename = os.path.join(atten_check_output_folder, f"{trait}_supp{column}_attenCheck.txt")
    with open(txt_filename, 'w') as txt_file:
        for i, pair in enumerate(atten_check_both):
            if i == len(atten_check_both) - 1:
                txt_file.write(' '.join(pair))
            else:
                txt_file.write(' '.join(pair) + '\n')

    module = [img_name for img_name in module if img_name not in atten_check_images]
    for i, index in enumerate(index_atten):
        module.insert(index, atten_check_images[i])

    # Save to text file
    with open(filename, 'w') as file:
        for i, item in enumerate(module):
            if i == len(module) - 1:
                file.write(str(item))
            else:
                file.write(f"{item}\n")


# Create backend file

In [66]:
import os

module_path = 'moduleStimuli_supp'
all_files = [f for f in os.listdir(module_path) if os.path.isfile(os.path.join(module_path, f)) and f.lower().endswith(('.txt'))]
text_files = [file[:-4] for file in all_files if file.endswith('.txt')]

In [68]:
# Write the list of text files to a text file
with open('BackEnd_CurrentCount.txt', 'w') as file:
    for i, text_file in enumerate(text_files):
        if i == len(text_files) - 1:
            file.write(f'{text_file} 0')
        else:
            file.write(f'{text_file} 0\n')

In [70]:
# shuffle lines
import random

# Function to shuffle lines in a file
def shuffle_lines_in_file(file_path):
    # Read lines from the file
    with open(file_path, 'r') as file:
        lines = file.readlines()

    # Shuffle the lines
    random.shuffle(lines)

    # Write shuffled lines back to the file
    with open(file_path, 'w') as file:
        file.writelines(lines)


file_path = 'BackEnd_CurrentCount.txt'
shuffle_lines_in_file(file_path)